# Preamble

In [16]:
import os, re
from importlib import reload
from posixpath import join, basename
from configparser import ConfigParser

import numpy as np
import pandas as pd
from collections import defaultdict as ddict

from firecloud.fiss import fapi as terra
from google.cloud.storage import Client

In [10]:
cdir = os.getcwd()
os.chdir(join('..', 'scripts'))
import kterra as kt
os.chdir(cdir)

In [3]:
%matplotlib

Using matplotlib backend: <object object at 0x0000017ECF14DA90>


In [31]:
cdir = os.getcwd()
os.chdir(join('..', 'scripts'))
reload(kt)
os.chdir(cdir)

In [3]:
gproject = "aldubayan-lab-dfci"
tproject = "DFCI-aldubayan-lab"
me = "kyler_anderson@mail.dfci.harvard.edu"
workspaces = {
    "Sample Scale": "KAnderson_PC_Germline_Analysis_WES",
    "Qatari Ref": "KAnderson_Qatari_WGS_Ref_Curation"
}

# Entity Work

In [20]:
ws.last_request.json()

[{'attributes': {'model_qc_string': 'PASS',
   'astrolabe_combined_output': 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/5a5c3574-b599-4c07-ab47-2a764965b5c1/MergeAstrolabeOutputs/b5e7ca0a-e0a9-46c6-916f-6a98b603f6e1/call-CombineFiles/astrolabe_combined.output.tsv',
   'per_sample_interval_fraction': 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/8d524218-74cc-46e6-95fa-b6b10c8d7b92/process_coverage_info/13372e26-3bb6-443d-bcda-85019a66c060/call-ProcessCoverageInfoIntervalTask/all_samples_interval_fraction_above_15_coverage_per_sample.tsv.gz',
   'subsetVCF_BreastCancer_only': 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/79293f9b-bb4e-491a-8429-1d464fc9dd9c/Subset_VCF/43e77afd-fde6-46f2-98ad-e3abc9ad8240/call-GATKSelectVariants/all_samples.subset.vcf.gz',
   'genotyped_segments_vcf_indexes_path_list': 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGermlineCohortWorkflow/578b5d62-ddc6-46ae-91e4-1a9bae69ef98/call-WriteSegmentIndexes/genotyped_segme

In [18]:
ws = kt.Workspace('arab_breast_cancer_study_wes')
ssets = ws.get_table('sample_set')

['gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGermlineCohortWorkflow/578b5d62-ddc6-46ae-91e4-1a9bae69ef98/call-GermlineCNVCallerCohortMode/shard-0/all_samples-gcnv-model-shard-0.tar.gz', 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGermlineCohortWorkflow/578b5d62-ddc6-46ae-91e4-1a9bae69ef98/call-GermlineCNVCallerCohortMode/shard-1/all_samples-gcnv-model-shard-1.tar.gz', 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGermlineCohortWorkflow/578b5d62-ddc6-46ae-91e4-1a9bae69ef98/call-GermlineCNVCallerCohortMode/shard-2/all_samples-gcnv-model-shard-2.tar.gz', 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGermlineCohortWorkflow/578b5d62-ddc6-46ae-91e4-1a9bae69ef98/call-GermlineCNVCallerCohortMode/shard-3/all_samples-gcnv-model-shard-3.tar.gz', 'gs://fc-d1a7d9c8-1823-49d3-ba8f-16218f42c04a/d5d7adee-348a-4641-8ae2-04eaaf8305cb/CNVGerml

In [23]:
ssets['gcnv_calls_tars']

id
all_samples                                            JSONEntry([['gs://fc-d1a7d9c8-1823-49d3-ba8f-1...
rs80359351_carriers                                                                                  NaN
test_sample_set                                                                                      NaN
liftover_2022-01-25T20-34-25                                                                         NaN
liftover_warn_on_missing_contig_2022-01-25T21-01-50                                                  NaN
MergeStargazerOutputs_2022-01-26T05-28-41                                                            NaN
GATK_Collect_Read_Counts_2022-02-16T01-47-58                                                         NaN
GATK_Collect_Read_Counts_2022-02-16T15-28-22                                                         NaN
BC_P_All_Female                                        JSONEntry([['gs://fc-d1a7d9c8-1823-49d3-ba8f-1...
BC_P_All_Female_Autosome_COHORT                     

In [4]:
ws = kt.Workspace(workspaces['Qatari Ref'])

In [5]:
entities = ws.get_table('population')

In [10]:
for eid, thing in entities[['common_phased_vcf_idx', 'rare_phased_vcf_idx']].iterrows():
  vcfs = list(thing)
  ws.update_entity('population', eid, phased_parts_idx=vcfs)

In [31]:
qlist = kt.reflist(qsamples.index, 'qat_sample')
klist = kt.reflist(kgsamples.index, '1kg_sample')


In [33]:
ws.update_entity('sample_set', '1KGQ', ksamples=klist)

: 

In [24]:
ws.get_table('sample_set')

samples  \
id                                                                                   
all                              [SRR2098177, SRR2098178, SRR2098179, SRR209818...   
doc2                                                      [SRR2098213, SRR2098268]   
Test_Set                                      [SRR2098177, SRR2098178, SRR2098179]   
Test_Set_2                                    [SRR2098180, SRR2098181, SRR2098182]   
T3                                            [SRR2098183, SRR2098184, SRR2098185]   
DeepVariant_2024-06-24T17-23-19  [SRR2098276, SRR2098274, SRR2098273, SRR209827...   
DeepVariant_2024-06-27T12-33-55  [SRR2098186, SRR2098187, SRR2098188, SRR209818...   

                                                                              pvcf  \
id                                                                                   
all                              gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
doc2                                                                          None   
Test_Set                                                                      None   
Test_Set_2                                                                    None   
T3                               gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
DeepVariant_2024-06-24T17-23-19  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
DeepVariant_2024-06-27T12-33-55                                               None   

                                                                          pvfc_idx  \
id                                                                                   
all                              gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
doc2                                                                          None   
Test_Set                                                                      None   
Test_Set_2                                                                    None   
T3                               gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
DeepVariant_2024-06-24T17-23-19  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
DeepVariant_2024-06-27T12-33-55                                               None   

                                                                     gln_resources  
id                                                                                  
all                              gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...  
doc2                                                                          None  
Test_Set                                                                      None  
Test_Set_2                                                                    None  
T3                               gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...  
DeepVariant_2024-06-24T17-23-19  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...  
DeepVariant_2024-06-27T12-33-55                                               None

In [30]:
ws.last_request.content

b'{"causes":[],"message":"inconsistent entity types for list: Vector(AttributeEntityReference(qat_sample,SRR2098177), AttributeEntityReference(qat_sample,SRR2098185), AttributeEntityReference(qat_sample,SRR2098188), AttributeEntityReference(qat_sample,SRR2098189), AttributeEntityReference(qat_sample,SRR2098192), AttributeEntityReference(qat_sample,SRR2098193), AttributeEntityReference(qat_sample,SRR2098198), AttributeEntityReference(qat_sample,SRR2098201), AttributeEntityReference(qat_sample,SRR2098205), AttributeEntityReference(qat_sample,SRR2098210), AttributeEntityReference(qat_sample,SRR2098223), AttributeEntityReference(qat_sample,SRR2098227), AttributeEntityReference(qat_sample,SRR2098228), AttributeEntityReference(qat_sample,SRR2098229), AttributeEntityReference(qat_sample,SRR2098232), AttributeEntityReference(qat_sample,SRR2098243), AttributeEntityReference(qat_sample,SRR2098247), AttributeEntityReference(qat_sample,SRR2098248), AttributeEntityReference(qat_sample,SRR2098250), 

# File maneuvering

## Within Bucket

In [ ]:
ws = kt.Workspace(workspaces["Qatari Ref"])
subs = ws.list_submissions()
sub = ws.get_submission(subs.index[0])

In [90]:
from posixpath import basename
from collections import defaultdict as ddict, Counter

table = 'sample'
preserve = [
    'cumulative_coverage_counts',
    'cumulative_coverage_proportions',
    'gene_statistics',
    'gene_summary',
    'interval_statistics',
    'interval_summary',
    'coverage_statistics',
    'coverage_summary']


dm = ws.get_table(table)
gbpref = ws.folder.cloud_path()

unique_file_map = dict()
updates = ddict(dict)

moved = []
missed = []

def process_val(v, e, c):
    if type(v) != str: return # not a string
    if not v.startswith(gbpref): return # not a bucket file path
    ws_file = v.removeprefix(gbpref)
    if ws_file.split('/')[0] != 'submissions': return # already moved
    
    if ws_file in unique_file_map:
        unique_file_map[ws_file][1].append((e, c))
        return
    
    # new file, to be stored in a subfolder based on the first column it's encountered in
    unique_file_map[ws_file] = [c, [(e, c)]]
    
def generate_destinations():
    # rearrange on c
    by_col = ddict(dict)
    for srce, (c, cells) in unique_file_map.items():
        by_col[c][srce] = cells

    for c, srce_links in by_col.items():
        prefix = join('ModelData', table, c)

        basemap = ddict(list)
        for srce in srce_links:
            basemap[basename(srce)].append(srce)

        share_i = 0
        for base, srces in basemap.items():
            if len(srces) == 1: # no threat of clobber
                unique_file_map[srces[0]][0] = join(prefix, base)
            else: # need to avoid clobber
                for srce in srces:
                    col_e = [e for e, cc in srce_links[srce] if cc == c]
                    if len(col_e) == 1: # if single col entry
                        unique_file_map[srce][0] = join(prefix, col_e[0], base)
                    else:
                        unique_file_map[srce][0] = join(prefix, f'{share_i}', base)
                        share_i += 1

for c in preserve:
    if c not in dm:
        print(f'Column {c} not found in {table} model')
        continue

    for e, v in dm[c].items():
        if type(v) == list:
            for t in v: process_val(t, e, c)
            updates[e][c] = dict()
        else:
            process_val(v, e, c)
            updates[e][c] = ''

generate_destinations()

In [8]:
max(Counter(v for v, c in unique_file_map.values()).values())

1

In [91]:
unique_file_map

{'submissions/f955dab1-d6ed-4392-9c4f-1a91cc46ae00/DepthOfCoverage/6f81ebf4-1ebb-4169-b9b4-f0c259a4c65f/call-depthOfCoverage/attempt-4/SRR2098177.sample_cumulative_coverage_counts': ['ModelData/sample/cumulative_coverage_counts/SRR2098177.sample_cumulative_coverage_counts',
  [('SRR2098177', 'cumulative_coverage_counts')]],
 'submissions/f955dab1-d6ed-4392-9c4f-1a91cc46ae00/DepthOfCoverage/5a53a431-b239-465b-a3a5-dda283e48c59/call-depthOfCoverage/SRR2098185.sample_cumulative_coverage_counts': ['ModelData/sample/cumulative_coverage_counts/SRR2098185.sample_cumulative_coverage_counts',
  [('SRR2098185', 'cumulative_coverage_counts')]],
 'submissions/f955dab1-d6ed-4392-9c4f-1a91cc46ae00/DepthOfCoverage/7cc95462-9157-42af-964a-422f92c48745/call-depthOfCoverage/attempt-4/SRR2098188.sample_cumulative_coverage_counts': ['ModelData/sample/cumulative_coverage_counts/SRR2098188.sample_cumulative_coverage_counts',
  [('SRR2098188', 'cumulative_coverage_counts')]],
 'submissions/f955dab1-d6ed-4392

In [92]:
print('moving files')
for srce, (dest, cells) in unique_file_map.items():
    if srce == dest: continue
    srce_blob = ws.folder.get_blob(srce)
    dest_blob = None
    try:
        ws.folder.gbucket.rename_blob(srce_blob, dest)
    except:
        print(f'Something went wrong moving {srce}')
        missed.append(srce)
        continue
    
    moved.append(srce)
    for e, c in cells:
        if type(updates[e][c]) == str: updates[e][c] = dest
        else: updates[e][c][srce] = dest # lists need to be updated weird

print('updating data model')
for e, vals in updates.items():
    attrs = {}
    for c, u in vals.items():
        if len(u) == 0: # for both strings and dictionaries
            continue

        if type(u) == dict():
            newlist = []
            for srce in dm[c][e]:
                if not srce.startswith(gbpref):
                    newlist.append(srce)
                    continue
                srce = srce.remove_prefix(gbpref)
                dest = join(gbpref, u.get(srce, srce))
                newlist.append(dest)
            attrs[c] = newlist

        elif type(u) == str:
            attrs[c] = join(gbpref, u)

    if len(attrs) != 0:
        ws.update_entity(table, e, **attrs)

moving files
updating data model


## Between Buckets

In [15]:
gclient = ws.folder.gbucket.client
archive_bucket_name = 'aldubayan-qatari-wgs-2024'
archive_bucket = gclient.get_bucket(archive_bucket_name)

In [34]:
from posixpath import relpath

samples = ws.get_table('sample')
pref = ws.folder.cloud_path()

for e, fqs in samples[['fq1', 'fq2']].iterrows():
    updates = {}
    for attr, fq in fqs.items():
        dest = join(e, basename(fq))
        srce_blob = ws.folder.gbucket.get_blob(relpath(fq, pref))
        ws.folder.gbucket.copy_blob(srce_blob, archive_bucket, dest)
        
        full_dest = join('gs://', archive_bucket_name, dest)
        updates[attr] = full_dest
    ws.update_entity('sample', e, **updates)

    

## Archiving

1. iterate workspaces `ws`
    1. make workspace folder `ws`
    1. write `ws` description to `ws/description.md`
    1. write remaining meta to `ws/meta.json`
    1. maintain transfer database to account
        - duplicate file entries across workspace
        - missing data-model files
    1. make workspace data folder `ws/data`
    1. iterate workspace data files `f`
        1. move `f` to archive `ws/data`
        1. update workspace data table
    1. write workspace data table to `ws/data-table.tsv`
    1. make workspace data-model folder `ws/data-model`
    1. iterate entity type `type`
        1. make entity-type folder `ws/data-model/type`
        1. iterate rows `ent`
            1. make entity folder `ws/data-model/type/ent`
            1. iterate columns `col`
                1. move entity data files to archive `ws/data-model/type/ent/col/basename`
            1. update entity in data-model
        1. write type table to `ws/data-model/type-table.tsv`

In [76]:
for k in ws.list_tables():
  res = terra.get_entities_tsv(ws.project, ws.name, k)
  print(res.headers['content-disposition'])

attachment; filename="sample.tsv"
attachment; filename="sample_set.zip"


In [74]:
url = f"workspaces/{ws.project}/{ws.name}/exportAttributesTSV"
res = terra.__get(url)

In [75]:
res.headers['content-disposition']

'attachment; filename="MID-Ciliopathies-Exome-workspace-attributes.tsv"'

In [42]:
ws = kt.Workspace('MID-Ciliopathies-Exome')

In [54]:
ws.attr_table['description'][0]

'Data repository for the dbGaP study Ciliopathies Exome Sequencing Initiative'

In [52]:
ws.metadata

{'workspace': {'authorizationDomain': [],
  'billingAccount': 'billingAccounts/01DC30-264DCD-B34E70',
  'bucketName': 'fc-40ad39cc-0a33-45a5-ac26-c350d9df770f',
  'cloudPlatform': 'Gcp',
  'createdBy': 'hchu@broadinstitute.org',
  'createdDate': '2021-12-03T15:23:32.883Z',
  'googleProject': 'terra-881a3ee1',
  'googleProjectNumber': '422197018088',
  'isLocked': False,
  'lastModified': '2024-06-07T22:21:23.039Z',
  'namespace': 'DFCI-aldubayan-lab',
  'state': 'Ready',
  'workflowCollectionName': '40ad39cc-0a33-45a5-ac26-c350d9df770f',
  'workspaceId': '40ad39cc-0a33-45a5-ac26-c350d9df770f',
  'workspaceType': 'rawls',
  'workspaceVersion': 'v2'}}

In [67]:
res = terra.get_workspace('vanallen-aldubayan-lab', 'QATR-1KG-Reference-Panel')

In [71]:
res.headers


{'Date': 'Tue, 28 Jan 2025 08:07:20 GMT', 'Server': 'Apache', 'X-Frame-Options': 'SAMEORIGIN', 'X-XSS-Protection': '1; mode=block', 'X-Content-Type-Options': 'nosniff', 'Strict-Transport-Security': 'max-age=31536000; includeSubDomains', 'Referrer-Policy': 'strict-origin-when-cross-origin', 'Cache-control': 'no-store', 'Pragma': 'no-cache', 'Access-Control-Allow-Origin': '*', 'Access-Control-Allow-Headers': 'authorization,content-type,accept,origin,x-app-id', 'Access-Control-Allow-Methods': 'GET,POST,PUT,PATCH,DELETE,OPTIONS,HEAD', 'Access-Control-Max-Age': '1728000', 'Vary': 'Accept-Encoding', 'Content-Encoding': 'gzip', 'Alt-Svc': 'h3=":443"; ma=2592000,h3-29=":443"; ma=2592000, h3=":443"; ma=2592000,h3-29=":443"; ma=2592000', 'Content-Type': 'application/json', 'Via': '1.1 google, 1.1 google', 'Transfer-Encoding': 'chunked'}

In [63]:
ws.last_request.headers['content-type']

'application/json'

In [23]:
tproject

'DFCI-aldubayan-lab'

## Submission Salvage

In [92]:
table = 'sample_set'
column = 'rare_phased_vcf'
columnidx = 'rare_phased_vcf_idx'
gb = ws.folder.gbucket

def rename_blob(f, namer=basename):
    f = f.removeprefix(pref)
    blob = gb.get_blob(f)
    nf = namer(f)
    gb.rename_blob(blob, nf)
    return join(pref, nf)

def my_renamer(f):
    return join('ModelData', table, column, basename(f))

In [ ]:
ss = ws.get_table(table)
for pop, (files, idxs) in ss[[column, columnidx]].iterrows():

    if type(files) == list:
        new_fn = kt.attlist([rename_blob(fn, my_renamer) for fn in files])
        new_ix = kt.attlist([rename_blob(fn, my_renamer) for fn in idxs])
    else:
        new_fn = rename_blob(files, my_renamer)
        new_ix = rename_blob(idxs, my_renamer)
    
    data = {
      column: new_fn,
      columnidx: new_ix
    }

    ws.update_entity(table, pop, **data)

In [ ]:
ss = ws.get_table(table)
for pop, files in ss[column].items():

    if type(files) == list:
        new_fn = kt.attlist([rename_blob(fn, my_renamer) for fn in files])
    else:
        new_fn = rename_blob(files, my_renamer)
    
    data = {
      column: new_fn,
    }

    ws.update_entity(table, pop, **data)

AttributeError: 'NoneType' object has no attribute 'removeprefix'

In [96]:
ws.update_entity(table, 'SAS', pvcf_stats = nn)

In [ ]:
nn = rename_blob(
    'gs://fc-383cdc04-2139-475e-ad85-406c08033859/ModelData/sample_set/pvcf_stats/AFR.stats.txt',
    lambda x: 'ModelData/sample_set/pvcf_stats/AFR.stats.txt')

ws.update_entity(table, 'AFR', pvcf_stats = nn)

In [ ]:
current_vcfs = [join(pref, f) for f in vcfs]
current_idxs = [join(pref, f) for f in idxs]

# Cost Table

In [6]:
from google.cloud import bigquery

In [7]:
queryClient = bigquery.Client('projectcostestimte')

In [8]:
query = """
SELECT
   ANY_VALUE(project.name) as pn, project.id,
   ANY_VALUE((SELECT value
              FROM UNNEST(project.labels)
              WHERE key = 'workspacename')) as workspacename,
  service.description as service, sum(cost) as YTD,
FROM `projectcostestimte.daily_cost.gcp_billing_export_v1_01DC30_264DCD_B34E70`
WHERE
  _PARTITIONTIME BETWEEN TIMESTAMP("2024-01-01") AND TIMESTAMP("2024-06-07")
GROUP BY project.id, service
HAVING service = 'Cloud Storage'
ORDER BY YTD DESC"""

In [9]:
for dataset in queryClient.list_datasets():
    print(dataset.dataset_id)

daily_cost


In [10]:
gbqDS = queryClient.get_dataset('projectcostestimte.daily_cost')
for t in queryClient.list_tables(gbqDS):
    print(t.table_id)

gcp_billing_export_v1_01DC30_264DCD_B34E70


In [11]:
qj = queryClient.query(query)

In [12]:
qj.state

'DONE'

In [13]:
qtable = qj.to_dataframe()
qtable

c:\Users\ka021\api\anaconda3\envs\py3.11\Lib\site-packages\google\cloud\bigquery\table.py:1727: UserWarning: BigQuery Storage module not found, fetch data with the REST endpoint instead.
  warnings.warn(


pn                              id  \
0   vanallen-aldubayan-lab--QATR-W                  terra-d7327e81   
1   vanallen-aldubayan-lab--QATR-1                  terra-af1a7acf   
2   DFCI-aldubayan-lab--MID-Ciliop                  terra-881a3ee1   
3   DFCI-aldubayan-lab--UKbio-cont                  terra-0df969ce   
4   DFCI-aldubayan-lab--KAnderson-                  terra-88b03bea   
5   vanallen-aldubayan-lab--arab-b                  terra-7036173e   
6   vanallen-aldubayan-lab--arab-b                  terra-d3c999a2   
7   DFCI-aldubayan-lab--An-Angiosa                  terra-b588851c   
8   DFCI-aldubayan-lab--KAnderson-                  terra-f64e23e8   
9   DFCI-aldubayan-lab--2022-CarT-                  terra-9ebea4f1   
10  DFCI-aldubayan-lab--KAnderson-                  terra-6524346e   
11  DFCI-aldubayan-lab--Dasman-Ins                  terra-e2f9491f   
12  DFCI-aldubayan-lab--KAnderson-                  terra-47075a46   
13  vanallen-aldubayan-lab--arab-b                  terra-d6c0baa5   
14  vanallen-aldubayan-lab--VanAll                  terra-cfa1b7e3   
15  DFCI-aldubayan-lab--UKB-Prosta                  terra-505abd81   
16  DFCI-aldubayan-lab--TCGA-BRCA-                  terra-46b708b9   
17  DFCI-aldubayan-lab--KAnderson-                  terra-a7f38bfa   
18  ArabBreastCancerProjectArchive  arabbreastcancerprojectarchive   
19              Aldubayan-lab-DFCI              aldubayan-lab-dfci   
20  DFCI-aldubayan-lab--arab-breas                  terra-968d3cde   
21  DFCI-aldubayan-lab--ALDUBAYAN-                  terra-a8d893d5   
22  vanallen-aldubayan-lab--arab-b                  terra-0b69de80   
23  vanallen-aldubayan-lab--PRS-Ma                  terra-46e8b1dd   
24  DFCI-aldubayan-lab--KAnderson-                  terra-63e3dc8c   
25  DFCI-aldubayan-lab--rjain-test                  terra-dfba15b5   
26  DFCI-aldubayan-lab--UKB-Prosta                  terra-8683ccbe   
27  DFCI-aldubayan-lab--Germline-A                  terra-730ce996   
28  vanallen-aldubayan-lab--UKbio-                  terra-8392b651   
29  vanallen-aldubayan-lab--germli                  terra-336dd9a6   
30  DFCI-aldubayan-lab--germline-I                  terra-f53bdaca   
31  DFCI-aldubayan-lab--Germline-A                  terra-848dfcb8   
32  vanallen-aldubayan-lab--1KG-WG                  terra-36811ab6   
33          vanallen-aldubayan-lab          vanallen-aldubayan-lab   

                                        workspacename        service  \
0                                            qatr-wes  Cloud Storage   
1                            qatr-1kg-reference-panel  Cloud Storage   
2                              mid-ciliopathies-exome  Cloud Storage   
3                               ukbio_control_storage  Cloud Storage   
4                   kanderson_qatari_wgs_ref_curation  Cloud Storage   
5                        arab_breast_cancer_study_wes  Cloud Storage   
6                                  arab_breast_cancer  Cloud Storage   
7                     an_angiosarcoma_rna_for_dr-copy  Cloud Storage   
8                  kanderson_pc_germline_analysis_wes  Cloud Storage   
9                       2022_cart_validation_migrated  Cloud Storage   
10               kanderson_pcgermline_cohortscale_dev  Cloud Storage   
11               dasman_institute_common_variant_data  Cloud Storage   
12               kanderson_multi-ancestry-prs_wes_1kg  Cloud Storage   
13                        arab_breast_cancer_analysis  Cloud Storage   
14    vanallen-aldubayan_13-325_germline_lipomas_copy  Cloud Storage   
15                        ukb_prostate_cancer_dec2022  Cloud Storage   
16  tcga_brca_controlledaccess_v1-0_data_2022_07_copy  Cloud Storage   
17               kanderson_pcgermline_samplescale_dev  Cloud Storage   
18                                               None  Cloud Storage   
19                                               None  Cloud Storage   
20                             arab_breast_cancer_cnv  Cloud Storage 

In [4]:
cost_table = pd.read_csv('anlaysis/gcloud_cost_table.csv')

In [13]:
cost_table.columns

Index(['Billing account name', 'Billing account ID', 'Project name',
       'Project ID', 'Project hierarchy', 'Service description', 'Service ID',
       'SKU description', 'SKU ID', 'Credit type', 'Cost type',
       'Usage start date', 'Usage end date', 'Usage amount', 'Usage unit',
       'Unrounded Cost ($)', 'Cost ($)'],
      dtype='object')

In [14]:
kt.fc_workspaces[kt.fc_workspaces['bucketName'] == 'fc-7130e767-a885-4678-95ed-7c966c79e2d0']

Empty DataFrame
Columns: [accessLevel, namespace, workspaceId, bucketName, createdBy, billingAccount, googleProject]
Index: []

In [51]:
t2 = kt.fc_workspaces[kt.fc_workspaces['billingAccount'] == 'billingAccounts/01DC30-264DCD-B34E70']
t2 = t2.reset_index().set_index('googleProject')

In [52]:
cols = ['Project ID', 'Unrounded Cost ($)']
t1 = cost_table[cols]\
    .groupby('Project ID')\
    .sum()\
    .sort_values('Unrounded Cost ($)', ascending=False)

In [57]:
t1.join(t2[['name','accessLevel', 'createdBy']], how='left').sort_values('Unrounded Cost ($)', ascending=False)

Unrounded Cost ($)  \
terra-88b03bea                         3406.637708   
terra-f64e23e8                          294.438595   
terra-d7327e81                          277.253030   
terra-af1a7acf                          223.037609   
terra-881a3ee1                          213.740538   
aldubayan-lab-dfci                      189.541335   
terra-0df969ce                          146.752655   
terra-d3c999a2                           63.160405   
terra-7036173e                           61.882871   
terra-9ebea4f1                           32.912665   
terra-cfa1b7e3                           32.174424   
terra-e2f9491f                           31.056313   
terra-47075a46                           30.806998   
terra-d6c0baa5                           23.784179   
terra-6524346e                           23.046250   
terra-b588851c                           20.608659   
terra-505abd81                           11.037217   
terra-46b708b9                            9.499753   
vanallen-aldubayan-lab                    6.740787   
arabbreastcancerprojectarchive            4.177739   
terra-968d3cde                            3.320436   
terra-a7f38bfa                            2.192252   
terra-a8d893d5                            1.461881   
terra-46e8b1dd                            0.801792   
terra-0b69de80                            0.460300   
terra-dfba15b5                            0.183804   
terra-8683ccbe                            0.181919   
terra-730ce996                            0.181556   
terra-8392b651                            0.181467   
terra-336dd9a6                            0.181467   
terra-36811ab6                            0.181463   
terra-848dfcb8                            0.181436   
terra-63e3dc8c                            0.181436   
terra-f53bdaca                            0.181436   
projectcostestimte                        0.000000   

                                                                             name  \
terra-88b03bea                                  KAnderson_Qatari_WGS_Ref_Curation   
terra-f64e23e8                                 KAnderson_PC_Germline_Analysis_WES   
terra-d7327e81                                                           QATR-WES   
terra-af1a7acf                                           QATR-1KG-Reference-Panel   
terra-881a3ee1                                             MID-Ciliopathies-Exome   
aldubayan-lab-dfci                                                            NaN   
terra-0df969ce                                              UKbio_control_storage   
terra-d3c999a2                                                 arab_breast_cancer   
terra-7036173e                                       arab_breast_cancer_study_wes   
terra-9ebea4f1                                      2022_CarT_validation_migrated   
terra-cfa1b7e3                                                                NaN   
terra-e2f9491f                               Dasman_Institute_Common_Variant_Data   
terra-47075a46                               KAnderson_Multi-Ancestry-PRS_WES_1KG   
terra-d6c0baa5                                        arab_breast_cancer_analysis   
terra-6524346e                               KAnderson_PCGermline_CohortScale_Dev   
terra-b588851c                                    An_Angiosarcoma_RNA_for_DR copy   
terra-505abd81                                        UKB_Prostate_Cancer_Dec2022   
terra-46b708b9                  TCGA_BRCA_ControlledAccess_V1-0_DATA_2022_07_Copy   
vanallen-aldubayan-lab                                                        NaN   
arabbreastcancerprojectarchive                                                NaN   
terra-968d3cde                                             arab_breast_cancer_cnv   
terra-a7f38bfa                               KAnderson_PCGermline_SampleScale_Dev   
terra-a8d893d5                                       ALDUBAYAN_Arab_PC_study_copy   
terra-46e8b1dd                                 

In [74]:
costc = ['Unrounded Cost ($)']
cols = ['Project ID', 'Service description']

the_table = cost_table[cols + costc].groupby(cols).sum()\
    .reset_index()\
    .pivot(columns='Service description', index='Project ID', values='Unrounded Cost ($)')\
    .join(t2[['name','accessLevel', 'createdBy']], how='outer')\
    .sort_values('Cloud Storage', ascending=False)

In [79]:
terraproj = the_table.index.str.startswith('terra')

In [81]:
the_table[~terraproj]

BigQuery  Cloud DNS  Cloud Logging  \
aldubayan-lab-dfci                   NaN        NaN            0.0   
arabbreastcancerprojectarchive       NaN        NaN            NaN   
vanallen-aldubayan-lab               NaN        NaN            0.0   
projectcostestimte                   0.0        NaN            0.0   

                                Cloud Storage  Compute Engine  Networking  \
aldubayan-lab-dfci                   8.067384      181.379871     0.09408   
arabbreastcancerprojectarchive       4.177739             NaN         NaN   
vanallen-aldubayan-lab               0.000000        6.740787         NaN   
projectcostestimte                        NaN             NaN         NaN   

                               name accessLevel createdBy  
aldubayan-lab-dfci              NaN         NaN       NaN  
arabbreastcancerprojectarchive  NaN         NaN       NaN  
vanallen-aldubayan-lab          NaN         NaN       NaN  
projectcostestimte              NaN         NaN       NaN

In [78]:
the_table[terraproj].sort_values('accessLevel')

BigQuery  Cloud DNS  Cloud Logging  Cloud Storage  \
terra-46b708b9       NaN   0.181436            NaN       9.318317   
terra-336dd9a6       NaN   0.181436            NaN       0.000031   
terra-88b03bea       NaN   5.443631            0.0     362.862295   
terra-63e3dc8c       NaN   0.181436            NaN            NaN   
terra-730ce996       NaN   0.181436            NaN       0.000120   
terra-8683ccbe       NaN   0.181436            NaN       0.000483   
terra-dfba15b5       NaN   0.181436            NaN       0.002368   
terra-a8d893d5       NaN   0.181570            NaN       1.280311   
terra-a7f38bfa       NaN   0.181436            NaN       2.010816   
terra-968d3cde       NaN   0.181570            NaN       3.138866   
terra-848dfcb8       NaN   0.181436            NaN            NaN   
terra-b588851c       NaN   0.181436            NaN      20.427223   
terra-505abd81       NaN   0.181570            NaN      10.855647   
terra-47075a46       NaN   0.181436            0.0      30.625562   
terra-e2f9491f       NaN   0.181436            NaN      30.874877   
terra-9ebea4f1       NaN   0.181436            NaN      32.731229   
terra-f64e23e8       NaN   6.692095            0.0      52.531927   
terra-0df969ce       NaN   0.181436            NaN     146.571219   
terra-881a3ee1       NaN   0.181436            NaN     213.559102   
terra-6524346e       NaN   0.181741            0.0      22.789667   
terra-f53bdaca       NaN   0.181436            NaN            NaN   
terra-d6c0baa5       NaN   0.181436            NaN      23.602743   
terra-d3c999a2       NaN   0.181436            NaN      60.997206   
terra-46e8b1dd       NaN   0.181436            NaN       0.620356   
terra-7036173e       NaN   0.181436            NaN      61.701435   
terra-36811ab6       NaN   0.181436            NaN       0.000027   
terra-d7327e81       NaN   0.181570            NaN     277.071460   
terra-8392b651       NaN   0.181436            NaN       0.000031   
terra-af1a7acf       NaN   0.181436            0.0     222.856173   
terra-cfa1b7e3       NaN   0.181436            0.0      20.099042   
terra-0b69de80       NaN   0.181436            0.0       0.278864   

                Compute Engine  Networking  \
terra-46b708b9             NaN         NaN   
terra-336dd9a6             NaN         NaN   
terra-88b03bea     3038.331782         0.0   
terra-63e3dc8c             NaN         NaN   
terra-730ce996             NaN         NaN   
terra-8683ccbe             NaN         NaN   
terra-dfba15b5             NaN         NaN   
terra-a8d893d5             NaN         NaN   
terra-a7f38bfa             NaN         NaN   
terra-968d3cde             NaN         NaN   
terra-848dfcb8             NaN         NaN   
terra-b588851c             NaN         NaN   
terra-505abd81             NaN         NaN   
terra-47075a46             NaN         NaN   
terra-e2f9491f             NaN         NaN   
terra-9ebea4f1             NaN         NaN   
terra-f64e23e8      235.214573         0.0   
terra-0df969ce             NaN         NaN   
terra-881a3ee1             NaN         NaN   
terra-6524346e        0.074842         0.0   
terra-f53bdaca             NaN         NaN   
terra-d6c0baa5             NaN         NaN   
terra-d3c999a2        1.981763         NaN   
terra-46e8b1dd             NaN         NaN   
terra-7036173e             NaN         NaN   
terra-36811ab6             NaN         NaN   
terra-d7327e81             NaN         NaN   
terra-8392b651             NaN         NaN   
terra-af1a7acf             NaN         NaN   
terra-cfa1b7e3       11.893946         NaN   
terra-0b69de80             NaN         NaN   

                                                             name  \
terra-46b708b9  TCGA_BRCA_ControlledAccess_V1-0_DATA_2022_07_Copy   
terra-336dd9a6                germline_common_variants_components   
terra-88b03bea                  KAnderson_Qatari_WGS_Ref_Curation   
terra-63e3dc8c             KAnderson_PC_Germline_Analysis_

# Submission Digging

In [9]:
sms = ws.list_submissions()
sms

methodconfigurationname  \
submissionId                                                          
cba1c0c6-e1c3-492e-b092-003c727a7c44              GLNexus_Scattered   
8dc9cf72-a981-4a22-b010-3f2c67acaf13  GLNexus_Scattered_aU-BGZa3wIs   
71999e74-dcdb-4d4c-a3db-92861f6ed013  GLNexus_Scattered_xJSl8l7F1bk   
5d75fa2f-a8c9-4b60-96d0-0b70fc3b8b19                       FillTags   
cfc6ea8f-14aa-46e1-8ec4-572c95497a7d                       FillTags   
...                                                             ...   
a8b9ddea-e9cb-427c-af15-6c0e09fa32a5         SRAToFastq_N1yDL1jUlZM   
8788f9cb-5b23-473e-83ef-1a215f0a5a0c         SRAToFastq_7c_wmlihbZA   
de061565-e541-4e76-b70e-68b4485e5f0b         SRAToFastq_1vJzi_ZrJoo   
96cdb06e-f39a-40df-9fef-2674c3ee6334         SRAToFastq_IqGuMYlYeY0   
88a35c61-1395-4a64-ae9f-06f81c97425e          SRA_Fetch_wwq8642Y450   

                                                                 date  \
submissionId                                                            
cba1c0c6-e1c3-492e-b092-003c727a7c44 2024-10-03 14:21:37.340000+00:00   
8dc9cf72-a981-4a22-b010-3f2c67acaf13 2024-10-03 14:07:22.793000+00:00   
71999e74-dcdb-4d4c-a3db-92861f6ed013 2024-10-02 21:34:15.246000+00:00   
5d75fa2f-a8c9-4b60-96d0-0b70fc3b8b19 2024-10-01 01:02:35.235000+00:00   
cfc6ea8f-14aa-46e1-8ec4-572c95497a7d 2024-10-01 01:00:46.862000+00:00   
...                                                               ...   
a8b9ddea-e9cb-427c-af15-6c0e09fa32a5 2024-05-20 22:17:47.023000+00:00   
8788f9cb-5b23-473e-83ef-1a215f0a5a0c 2024-05-18 00:06:58.537000+00:00   
de061565-e541-4e76-b70e-68b4485e5f0b 2024-05-17 23:41:52.377000+00:00   
96cdb06e-f39a-40df-9fef-2674c3ee6334 2024-05-17 23:33:11.359000+00:00   
88a35c61-1395-4a64-ae9f-06f81c97425e 2024-05-16 22:26:35.101000+00:00   

                                       status  \
submissionId                                    
cba1c0c6-e1c3-492e-b092-003c727a7c44     Done   
8dc9cf72-a981-4a22-b010-3f2c67acaf13  Aborted   
71999e74-dcdb-4d4c-a3db-92861f6ed013  Aborted   
5d75fa2f-a8c9-4b60-96d0-0b70fc3b8b19     Done   
cfc6ea8f-14aa-46e1-8ec4-572c95497a7d     Done   
...                                       ...   
a8b9ddea-e9cb-427c-af15-6c0e09fa32a5     Done   
8788f9cb-5b23-473e-83ef-1a215f0a5a0c     Done   
de061565-e541-4e76-b70e-68b4485e5f0b  Aborted   
96cdb06e-f39a-40df-9fef-2674c3ee6334  Aborted   
88a35c61-1395-4a64-ae9f-06f81c97425e     Done   

                                                                                   root  \
submissionId                                                                              
cba1c0c6-e1c3-492e-b092-003c727a7c44  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
8dc9cf72-a981-4a22-b010-3f2c67acaf13  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
71999e74-dcdb-4d4c-a3db-92861f6ed013  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
5d75fa2f-a8c9-4b60-96d0-0b70fc3b8b19  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
cfc6ea8f-14aa-46e1-8ec4-572c95497a7d  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
...                                                                                 ...   
a8b9ddea-e9cb-427c-af15-6c0e09fa32a5  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
8788f9cb-5b23-473e-83ef-1a215f0a5a0c  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
de061565-e541-4e76-b70e-68b4485e5f0b  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
96cdb06e-f39a-40df-9fef-2674c3ee6334  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   
88a35c61-1395-4a64-ae9f-06f81c97425e  gs://fc-383cdc04-2139-475e-ad85-406c08033859/s...   

                                                                 entityname  \
submissionId                                                                  
cba1c0c6-e1c3-492e-b092-003c727a7c44  GLNexus_Scattered_2024-10-02T21-32-06   
8dc9cf72-a981-4a22-b010-3f2c67acaf13  GLNexus_Scattered_2024-10-02T21-32-06   
71999e74-dcdb-4d4c-a3db-92861f6e

In [10]:
gln_sm = ws.get_submission(sms.index[0])

In [12]:
gln_sm.workflows

status        cost entityName  \
workflowId                                                               
d68bcf43-e806-4e2a-830e-4d69f0c4b3c4     Failed   27.716810        AFR   
6f4bb6cc-9786-420c-9610-33b261a0e2b6  Succeeded   81.980290        AMR   
9c7aabbd-c4bb-4eee-9416-74ec4ae625eb  Succeeded  127.687065        EUR   
4f94bbad-b87c-44ab-acb1-13335ee7deea  Succeeded  113.160255        SAS   

                                          entityType messages  
workflowId                                                     
d68bcf43-e806-4e2a-830e-4d69f0c4b3c4  1kg_sample_set       []  
6f4bb6cc-9786-420c-9610-33b261a0e2b6  1kg_sample_set       []  
9c7aabbd-c4bb-4eee-9416-74ec4ae625eb  1kg_sample_set       []  
4f94bbad-b87c-44ab-acb1-13335ee7deea  1kg_sample_set       []

In [13]:
afr_gln = gln_sm.get_workflow(gln_sm.workflows.index[0])

In [15]:
wfmeta = afr_gln.get_metadata()

In [19]:
splitvcf_calls = wfmeta['calls']['GLNexus.SplitVcfs']

In [30]:
shard_indices = {}
for e, call in enumerate(splitvcf_calls):
    a = call['attempt']
    i = call['shardIndex']

    if i in shard_indices and \
       shard_indices[i][0] > a: continue
    
    shard_indices[i] = (a, e)

skeys = np.array(list(shard_indices.keys()))
if sum(skeys - np.arange(len(skeys))) == 0:
    print('Flattening shard_indices to list')
    shard_indices = list(shard_indices.values())


Flattening shard_indices to list


In [25]:
kt.agg_keys([splitvcf_calls[shard_indices[0][1]]])

{'attempt',
 'backend',
 'backendLabels.cromwell-workflow-id',
 'backendLabels.terra-submission-id',
 'backendLabels.wdl-call-alias',
 'backendLabels.wdl-task-name',
 'backendLogs.log',
 'backendStatus',
 'callCaching.allowResultReuse',
 'callCaching.effectiveCallCachingMode',
 'callCaching.hashes.backend name',
 'callCaching.hashes.command template',
 'callCaching.hashes.input count',
 'callCaching.hashes.input.File scatter_regions',
 'callCaching.hashes.input.File vcf',
 'callCaching.hashes.input.File vcf_idx',
 'callCaching.hashes.input.Float mem_gb',
 'callCaching.hashes.input.Int cpu',
 'callCaching.hashes.input.Int disk_gb',
 'callCaching.hashes.input.String bcftools_docker',
 'callCaching.hashes.input.String out_prefix',
 'callCaching.hashes.output count',
 'callCaching.hashes.output expression.Array(File) vcf_shard_idxs',
 'callCaching.hashes.output expression.Array(File) vcf_shards',
 'callCaching.hashes.runtime attribute.continueOnReturnCode',
 'callCaching.hashes.runtime att

In [36]:
call_keys = ['attempt', 'backendStatus', 'executionStatus', 'returnCode', 'inputs.vcf_idx']

sdf = kt.tabulate([splitvcf_calls[e] for a, e in shard_indices], call_keys)

In [37]:
failed = sdf[sdf.backendStatus != 'Success']
failed

attempt backendStatus   executionStatus  returnCode  \
21         1     Preempted  RetryableFailure         NaN   
38         2     Preempted  RetryableFailure         NaN   
44         3     Preempted  RetryableFailure         NaN   
50         1     Preempted  RetryableFailure         NaN   
56         1     Preempted  RetryableFailure         NaN   
..       ...           ...               ...         ...   
857        1     Preempted  RetryableFailure         NaN   
865        2     Preempted  RetryableFailure         NaN   
870        1     Preempted  RetryableFailure         NaN   
874        2     Preempted  RetryableFailure         NaN   
886        2     Preempted  RetryableFailure         NaN   

                                        inputs.vcf_idx  
21   gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
38   gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
44   gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
50   gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
56   gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
..                                                 ...  
857  gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
865  gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
870  gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
874  gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  
886  gs://fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e/C...  

[88 rows x 5 columns]

In [65]:
gclient = kt.clients[gproject]

In [83]:
from posixpath import commonpath, relpath, basename
import zoneinfo as tz

In [33]:
kgss = ws.get_table('1kg_sample')

In [82]:
#filelist = failed['inputs.vcf_idx']
filelist = kgss['gvcf_idx']

cpref = commonpath(list(filelist))
b = cpref[4:].split('/')[0]

kgbf = kt.BucketFolder(gclient.get_bucket(b), '')
kgcb = kgbf.gbucket
print('Bucket:', kgcb.path)
print('Found Bucket:', kgcb.exists())
print('Requester Pays:', kgcb.requester_pays)
print('Created:', kgcb.time_created.astimezone(tz.ZoneInfo('America/New_York')).strftime('%c'))

Bucket: /b/fc-56ac46ea-efc4-4683-b6d5-6d95bed41c5e
Found Bucket: True
Requester Pays: True
Created: Thu Feb 15 10:25:59 2024


In [85]:
cloud_base = kgbf.cloud_path()

missing = []
for f in filelist:
    rel = relpath(f, cloud_base)
    if kgbf.get_blob(rel) == None:
        missing.append(basename(f).split('.')[0])

In [86]:
missing

['NA18874']

# Workspace Meta

In [6]:
wsl = kt.fc_workspaces
wsl[wsl.bucketName == 'fc-b7d49b98-af79-47c6-a0dd-18ce16c888fb']

accessLevel               namespace  \
name                                                     
arab_breast_cancer      READER  vanallen-aldubayan-lab   

                                             workspaceId  \
name                                                       
arab_breast_cancer  b7d49b98-af79-47c6-a0dd-18ce16c888fb   

                                                 bucketName  \
name                                                          
arab_breast_cancer  fc-b7d49b98-af79-47c6-a0dd-18ce16c888fb   

                                      createdBy  \
name                                              
arab_breast_cancer  breardon@broadinstitute.org   

                                          billingAccount   googleProject  
name                                                                      
arab_breast_cancer  billingAccounts/01DC30-264DCD-B34E70  terra-d3c999a2

In [65]:
ws = kt.Workspace(workspaces['Qatari Ref'])

In [66]:
ws.get_workspace_data()

hg38_wg_regions  \
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...   

                          hg38_chromosome_chunks_4cM  \
0  [gs://fc-383cdc04-2139-475e-ad85-406c08033859/...   

                      __DESCRIPTION__hg38_wg_regions  \
0  regions file compatible with bcftools +scatter...   

  __DESCRIPTION__hg38_chromosome_maps  \
0   chromosome map files for shapeit5   

                          hg38_chromosome_arm_chunks  \
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...   

                                         description  \
0  Whole genome sequence analysis of 109 Qatari s...   

                                hg38_chromosome_maps  \
0  [gs://fc-383cdc04-2139-475e-ad85-406c08033859/...   

          __DESCRIPTION__hg38_chromosome_chunks_20cM  \
0  chromosome chunk files for shapeit5 phase_comm...   

                                         hg38_wg_bed  \
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...   

                                    sra_refseqs_hg19  \
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...   

                         hg38_chromosome_chunks_20cM  \
0  [gs://fc-383cdc04-2139-475e-ad85-406c08033859/...   

           __DESCRIPTION__hg38_chromosome_chunks_4cM  \
0  chromosome chunk files for shapeit5 phase_rare...   

                                           gene_list  \
0  gs://fc-394ae7b8-0dad-4d5f-a8cb-b9d74d23f954/U...   

                                        1KGQ_pop_tsv  \
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...   

                                name  \
0  KAnderson_Qatari_WGS_Ref_Curation   

                                         hail_script  
0  gs://fc-383cdc04-2139-475e-ad85-406c08033859/W...

In [41]:
names_lower = """bsun_seq_kit_test
arab_breast_cancer_study_wes-copy
ukbio_control_storage
bsun_ufc_wgs_test
bsun_germline_io_analysis_3_regional_io_only-copy
germline_common_variants_components
1kg-wgs-deepvariant
tcga_brca_controlledaccess_v1-0_data_2022_07_copy
prs_machinelearning
kanderson_multi-ancestry-prs_wes_1kg
bsun_1kg_imputation
ukb_prostate_cancer_dec2022
bsun_germline_io_analysis_kathleen_copy_pancancer
bsun_germline_io_analysis_3_regional_copy
bsun_r2000_all_io_normal
bsun_germline_io_analysis_3_melanoma_normal
kanderson_pc_germline_analysis_storage
kanderson_pcgermline_cohortscale_dev
arab_breast_cancer_study_wes
germline_analysis_methods
bsun_r2000_normal_io_only
bsun_germline_io_analysis_3_regional_io_only
ukbio_control_37k
germline_aldubayan_chinsky_nimbus_data_repo
ukb_prostate_cancer_dec2022_glnexus_test
mid-ciliopathies-exome
kanderson_qatari_wgs_ref_curation
bsun_r2000_wes
arab_breast_cancer_cnv
bsun_germline_io_analysis_3_io_response
2022_cart_validation_migrated
kanderson_pcgermline_samplescale_dev
aldubayan_arab_pc_study_copy
qatr-1kg-reference-panel
an_angiosarcoma_rna_for_dr-copy
vanallen-aldubayan_13-325_germline_lipomas_copy
arab_breast_cancer
arab_breast_cancer_analysis
qatr-wes
rjain_test
dasman_institute_common_variant_data
bsun_germline_io_analysis_3_regional_new_kidney_normal
bsun_germline_io_analysis_3_melanoma
germline_io_analysis_3_regional_kathleen
kanderson_pc_germline_analysis_wes""".split('\n')

In [37]:
wsl[wsl.namespace == 'DFCI-aldubayan-lab'].sort_index()

accessLevel  \
name                                                                
2022_CarT_validation_migrated                       PROJECT_OWNER   
ALDUBAYAN_Arab_PC_study_copy                        PROJECT_OWNER   
An_Angiosarcoma_RNA_for_DR copy                     PROJECT_OWNER   
BSun_1KG_imputation                                 PROJECT_OWNER   
BSun_R2000_WES                                      PROJECT_OWNER   
BSun_R2000_all_IO_normal                            PROJECT_OWNER   
BSun_germline_IO_analysis_3_regional_copy           PROJECT_OWNER   
Bsun_UFC_WGS_test                                   PROJECT_OWNER   
Bsun_germline_IO_analysis_3_melanoma                PROJECT_OWNER   
Bsun_germline_IO_analysis_3_melanoma_normal         PROJECT_OWNER   
Bsun_germline_IO_analysis_3_regional_IO_only        PROJECT_OWNER   
Bsun_germline_IO_analysis_3_regional_new_kidney...  PROJECT_OWNER   
Dasman_Institute_Common_Variant_Data                PROJECT_OWNER   
Germline_AlDubayan_Chinsky_NIMBUS_Data_Repo         PROJECT_OWNER   
Germline_Analysis_Methods                           PROJECT_OWNER   
KAnderson_Multi-Ancestry-PRS_WES_1KG                PROJECT_OWNER   
KAnderson_PCGermline_CohortScale_Dev                PROJECT_OWNER   
KAnderson_PCGermline_SampleScale_Dev                PROJECT_OWNER   
KAnderson_PC_Germline_Analysis_WES                  PROJECT_OWNER   
KAnderson_Qatari_WGS_Ref_Curation                   PROJECT_OWNER   
MID-Ciliopathies-Exome                              PROJECT_OWNER   
TCGA_BRCA_ControlledAccess_V1-0_DATA_2022_07_Copy       NO ACCESS   
UKB_Prostate_Cancer_Dec2022                         PROJECT_OWNER   
UKB_Prostate_Cancer_Dec2022_GLNexus_Test            PROJECT_OWNER   
UKbio_control_storage                               PROJECT_OWNER   
arab_breast_cancer_cnv                              PROJECT_OWNER   
germline_IO_analysis_3_regional_kathleen            PROJECT_OWNER   
rjain_test                                          PROJECT_OWNER   

                                                             namespace  \
name                                                                     
2022_CarT_validation_migrated                       DFCI-aldubayan-lab   
ALDUBAYAN_Arab_PC_study_copy                        DFCI-aldubayan-lab   
An_Angiosarcoma_RNA_for_DR copy                     DFCI-aldubayan-lab   
BSun_1KG_imputation                                 DFCI-aldubayan-lab   
BSun_R2000_WES                                      DFCI-aldubayan-lab   
BSun_R2000_all_IO_normal                            DFCI-aldubayan-lab   
BSun_germline_IO_analysis_3_regional_copy           DFCI-aldubayan-lab   
Bsun_UFC_WGS_test                                   DFCI-aldubayan-lab   
Bsun_germline_IO_analysis_3_melanoma                DFCI-aldubayan-lab   
Bsun_germline_IO_analysis_3_melanoma_normal         DFCI-aldubayan-lab   
Bsun_germline_IO_analysis_3_regional_IO_only        DFCI-aldubayan-lab   
Bsun_germline_IO_analysis_3_regional_new_kidney...  DFCI-aldubayan-lab   
Dasman_Institute_Common_Variant_Data                DFCI-aldubayan-lab   
Germline_AlDubayan_Chinsky_NIMBUS_Data_Repo         DFCI-aldubayan-lab   
Germline_Analysis_Methods                           DFCI-aldubayan-lab   
KAnderson_Multi-Ancestry-PRS_WES_1KG                DFCI-aldubayan-lab   
KAnderson_PCGermline_CohortScale_Dev                DFCI-aldubayan-lab   
KAnderson_PCGermline_SampleScale_Dev                DFCI-aldubayan-lab   
KAnderson_PC_Germline_Analysis_WES                  DFCI-aldubayan-lab   
KAnderson_Qatari_WGS_Ref_Curation                   DFCI-aldubayan-lab   
MID-Ciliopathies-Exome                              DFCI-aldubayan-lab   
TCGA_BRCA_ControlledAccess_V1-0_DATA_2022_07_Copy   DFCI-aldubayan-lab   
UKB_Prostate_Cancer_Dec2022                         DFCI-aldubayan-lab   
UKB_Prostate_Cancer_Dec2022_GLNexus_Test            DFCI-aldubayan-lab   
UKbio_control_storage                               DFCI-al

In [48]:
kt.Workspace('arab_breast_cancer_')

IndexError: list index out of range